Lecture 3: Multi-Table SQL
==========================

In [1]:
%load_ext sql
%sql sqlite://

/Users/tamalbiswas/anaconda/lib/python3.5/site-packages/numexpr/cpuinfo.py:76: UserWarning: [Errno 2] No such file or directory: 'sysctl'
  stacklevel=stacklevel + 1):


'Connected: None@None'

Joins!
------
Let's illustrate some more complex queries that join two tables together.

* Consider a table of companies, stock price, and HQ country.
> company(<u>cname</u>, stockprice, country)
 
* we'll then revist products and introduce some consistency requirements 

In [2]:
%%sql
drop table if exists product; -- This needs to be dropped if exists, see why further down!
drop table if exists company;
create table company (
    cname varchar primary key, -- company name uniquely identifies the company.
    stockprice money, -- stock price is in money 
    country varchar); -- country is just a string
insert into company values ('GizmoWorks', 25.0, 'USA');
insert into company values ('Canon', 65.0, 'Japan');
insert into company values ('Hitachi', 15.0, 'Japan');

Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.


[]

In [3]:
%sql select * from company;

Done.


[('GizmoWorks', 25, 'USA'), ('Canon', 65, 'Japan'), ('Hitachi', 15, 'Japan')]

Foreign Key Constraints
-----------------------
* Suppose that we want to create a products table

> Product(pname, price, category, manufacturer)

* Something is odd here: We can have manufacturers that sell products but don't occur in our company table!
* To protect against, this we introduce _foreign keys_ 

We say the company name in products _refers_ to cname in company. Let's do it in SQL! the key statement below is:

> foreign key (manufacturer) references company(cname)

  * Note that cname must be a key in company! 
  * Keys and Foreign keys come up _all_ the time. 
    * PKs and FKs are common (others, less so)

In [4]:
%%sql drop table if exists product;
pragma foreign_keys = ON; -- WARNING by default off in sqlite
create table product(
       pname varchar primary key, -- name of the product
       price money, -- price of the product
       category varchar, -- category
       manufacturer varchar, -- manufacturer
       foreign key (manufacturer) references company(cname));

insert into product values('Gizmo', 19.99, 'Gadgets', 'GizmoWorks');
insert into product values('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks');
insert into product values('SingleTouch', 149.99, 'Photography', 'Canon');
insert into product values('MultiTouch', 203.99, 'Household', 'Hitachi');


Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


[]

Indeed foreign keys are a _constraint_ 
> What happens if we introduce a company name not in our table?


In [5]:
try:
    %sql insert into product values('MultiTouch', 203.99, 'Household', 'Google');
except Exception as e:
    print (e)
    print ("Rejected!")

(sqlite3.IntegrityError) UNIQUE constraint failed: product.pname [SQL: "insert into product values('MultiTouch', 203.99, 'Household', 'Google');"]
Rejected!


In [6]:
%%sql
-- the update is rejected!
select * from product;

Done.


[('Gizmo', 19.99, 'Gadgets', 'GizmoWorks'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks'),
 ('SingleTouch', 149.99, 'Photography', 'Canon'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi')]

Foreign Keys and Delete
=============

* What happens if we delete a company? Other options:
  * Disallow the delete. (default)
  * Remove all products (add "`on delete cascade`")

  

**First option (default)- delete is disallowed**

In [7]:
try:
    %sql delete from company where cname = 'Hitachi';
except Exception as e:
    print (e)
    print ("Disallowed!")

(sqlite3.IntegrityError) FOREIGN KEY constraint failed [SQL: "delete from company where cname = 'Hitachi';"]
Disallowed!


**Second option: remove all products belonging to the company we delete**

Try adjusting the foreign key constraint clause when you create the products table as follows:
> foreign key (manufacturer) references company(cname) on delete cascade

Now, when a company row is deleted, all of the products linked by the foreign key constraint will be deleted as well.

In [3]:
%%sql
drop table if exists product; -- This needs to be dropped if exists, see why further down!
drop table if exists company;
create table company (
    cname varchar primary key, -- company name uniquely identifies the company.
    stockprice money, -- stock price is in money 
    country varchar); -- country is just a string
insert into company values ('GizmoWorks', 25.0, 'USA');
insert into company values ('Canon', 65.0, 'Japan');
insert into company values ('Hitachi', 15.0, 'Japan');
pragma foreign_keys = ON; -- WARNING by default off in sqlite
create table product(
       pname varchar primary key, -- name of the product
       price money, -- price of the product
       category varchar, -- category
       manufacturer varchar, -- manufacturer
       foreign key (manufacturer) references company(cname) on delete cascade);

insert into product values('Gizmo', 19.99, 'Gadgets', 'GizmoWorks');
insert into product values('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks');
insert into product values('SingleTouch', 149.99, 'Photography', 'Canon');
insert into product values('MultiTouch', 203.99, 'Household', 'Hitachi');

Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


[]

In [4]:
try:
    %sql delete from company where cname = 'Hitachi';
except Exception as e:
    print (e)
    print ("Disallowed!")

1 rows affected.


In [5]:
%sql select * from company;

Done.


[('GizmoWorks', 25, 'USA'), ('Canon', 65, 'Japan')]

In [6]:
%sql select * from product;

Done.


[('Gizmo', 19.99, 'Gadgets', 'GizmoWorks'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks'),
 ('SingleTouch', 149.99, 'Photography', 'Canon')]

Joins!
------
> Product (<u>pname</u>,  price, category, manufacturer)<br>
> Company (<u>cname</u>, stockPrice, country)

The query we want to answer is:

> Find all products under $200 manufactured in Japan;
> return their names and prices. 

Notice products don't have a location and manufacturers don't have price. Need info in _each_ of the tables.

## Creating these tables again

In [7]:
%%sql
drop table if exists product; -- This needs to be dropped if exists, see why further down!
drop table if exists company;
create table company (
    cname varchar primary key, -- company name uniquely identifies the company.
    stockprice money, -- stock price is in money 
    country varchar); -- country is just a string
insert into company values ('GizmoWorks', 25.0, 'USA');
insert into company values ('Canon', 65.0, 'Japan');
insert into company values ('Hitachi', 15.0, 'Japan');
pragma foreign_keys = ON; -- WARNING by default off in sqlite
create table product(
       pname varchar primary key, -- name of the product
       price money, -- price of the product
       category varchar, -- category
       manufacturer varchar, -- manufacturer
       foreign key (manufacturer) references company(cname) on delete cascade);

insert into product values('Gizmo', 19.99, 'Gadgets', 'GizmoWorks');
insert into product values('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks');
insert into product values('SingleTouch', 149.99, 'Photography', 'Canon');
insert into product values('MultiTouch', 203.99, 'Household', 'Hitachi');

Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


[]

In [8]:
%%sql 
SELECT * from product, company;

Done.


[('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'GizmoWorks', 25, 'USA'),
 ('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'Canon', 65, 'Japan'),
 ('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'Hitachi', 15, 'Japan'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'GizmoWorks', 25, 'USA'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'Canon', 65, 'Japan'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'Hitachi', 15, 'Japan'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'GizmoWorks', 25, 'USA'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'Canon', 65, 'Japan'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'Hitachi', 15, 'Japan'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'GizmoWorks', 25, 'USA'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'Canon', 65, 'Japan'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'Hitachi', 15, 'Japan')]

In [9]:
%%sql 
SELECT * from product JOIN company;

Done.


[('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'GizmoWorks', 25, 'USA'),
 ('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'Canon', 65, 'Japan'),
 ('Gizmo', 19.99, 'Gadgets', 'GizmoWorks', 'Hitachi', 15, 'Japan'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'GizmoWorks', 25, 'USA'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'Canon', 65, 'Japan'),
 ('PowerGizmo', 29.99, 'Gadgets', 'GizmoWorks', 'Hitachi', 15, 'Japan'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'GizmoWorks', 25, 'USA'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'Canon', 65, 'Japan'),
 ('SingleTouch', 149.99, 'Photography', 'Canon', 'Hitachi', 15, 'Japan'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'GizmoWorks', 25, 'USA'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'Canon', 65, 'Japan'),
 ('MultiTouch', 203.99, 'Household', 'Hitachi', 'Hitachi', 15, 'Japan')]

In [10]:
%%sql
SELECT pname, price
FROM product, company
where manufacturer=cname and country='Japan' and price <= 200;

Done.


[('SingleTouch', 149.99)]

In [11]:
%%sql
SELECT pname, price
FROM product
JOIN Company ON manufacturer=cname AND country='Japan' 
WHERE price <= 200;

Done.


[('SingleTouch', 149.99)]

In [12]:
%%sql
SELECT pname, price
FROM product
JOIN Company ON manufacturer=cname AND country='Japan'  AND price <=200;


Done.


[('SingleTouch', 149.99)]

Let's see how to write this join in a modular way.

In [68]:
%%sql -- Part 1: Set of Japanese companies.
SELECT distinct cname -- do we need distinct?
from company where country='Japan';

Done.


[('Canon',), ('Hitachi',)]

In [69]:
%%sql -- Part 2: Cheap Products (under $200)
select distinct pname, price, manufacturer
from product
where price <= 200;

Done.


[('Gizmo', 19.99, 'GizmoWorks'),
 ('PowerGizmo', 29.99, 'GizmoWorks'),
 ('SingleTouch', 149.99, 'Canon')]

In [70]:
%%sql -- combine them with nested SFW queries... this is a cross product?
SELECT * 
FROM 
  (SELECT DISTINCT pname, price, manufacturer
   FROM product
   WHERE price <= 200) CheapProducts,
  (SELECT DISTINCT cname
   FROM company
   WHERE country='Japan') JapaneseProducts;

Done.


[('Gizmo', 19.99, 'GizmoWorks', 'Canon'),
 ('Gizmo', 19.99, 'GizmoWorks', 'Hitachi'),
 ('PowerGizmo', 29.99, 'GizmoWorks', 'Canon'),
 ('PowerGizmo', 29.99, 'GizmoWorks', 'Hitachi'),
 ('SingleTouch', 149.99, 'Canon', 'Canon'),
 ('SingleTouch', 149.99, 'Canon', 'Hitachi')]

In [71]:
%%sql
-- Combine them as a join!
SELECT DISTINCT pname, price
FROM 
  (SELECT DISTINCT pname, price, manufacturer
   FROM product
   WHERE price <= 200) CheapProducts,
  (SELECT distinct cname
   FROM company
   WHERE country='Japan') JapaneseProducts
WHERE cname = manufacturer;

Done.


[('SingleTouch', 149.99)]

Takeways
--------
* There are potentially _many logically equivalent ways_ to write a query
    * This fact will be used later by the query optimizer
    * On exams, write the simplest thing

Duplicate answers from join
--------------------------

Note that we can get duplicate answers from a join...

In [74]:
%%sql -- duplicate answer
SELECT Country
FROM Product, Company
WHERE  Manufacturer=CName AND Category='Gadgets';

Done.


[('USA',), ('USA',)]